In [1]:
import lightgbm as lgb
from sklearn.grid_search import GridSearchCV
import time
import numpy as np
from sklearn.model_selection import train_test_split

D:\Anaconda3\lib\site-packages\sklearn\cross_validation.py:44: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)
D:\Anaconda3\lib\site-packages\sklearn\grid_search.py:43: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. This module will be removed in 0.20.
  DeprecationWarning)


In [2]:
import pandas as pd
data_tree_train = pd.read_csv('data_tree_train.csv',encoding='gbk')
data_tree_test = pd.read_csv('data_tree_test.csv',encoding='gbk')
data_tree_train_1 = data_tree_train[data_tree_train['label']==1]
data_tree_train_0 = data_tree_train[data_tree_train['label']==0]

gbdtTrain0, otherTrain0 = train_test_split(data_tree_train_0, test_size=0.5)
gbdtTrain1, otherTrain1 = train_test_split(data_tree_train_1, test_size=0.5)

gbdtTrain1 = gbdtTrain1.sample(6000,replace=True)
otherTrain1 = otherTrain1.sample(6000,replace=True)

gbdtTrain = pd.concat([gbdtTrain1,gbdtTrain0],ignore_index=True)
otherTrain = pd.concat([otherTrain1,otherTrain0],ignore_index=True)

In [6]:
pd.set_option('display.max_colwidth',100)
pd.set_option('display.max_columns', 1000)

In [7]:
target='label'
IDcol = '个人编码'
predictors = [x for x in data_tree_train.columns if x not in [target, IDcol]]

In [8]:
start = time.time()
param_test1 = {
#     'scale_pos_weight':np.array([1,5,7,10])
#     'max_depth':np.array([5,10,20,30]),
#     'min_child_weight':np.array([1,3,5,10]),
#     'gamma':[i/10.0 for i in range(0,5)],
#     'n_estimators':np.array([100,200,500]),
#     'boosting_type':['gbdt','dart']
#     'learning_rate':np.array([0.1,0.3])
#     'reg_alpha':np.array([1,0])
#     'num_leaves':np.array([16,20,24,28])
}
gsearch1 = GridSearchCV(estimator = lgb.LGBMClassifier( boosting_type='gbdt', num_leaves=31, max_depth=10, 
                                                       learning_rate=0.1, n_estimators=128, max_bin=255, subsample_for_bin=50000, 
                                                       min_split_gain=0, min_child_weight=1, min_child_samples=10, 
                                                       subsample=1, subsample_freq=1, colsample_bytree=1, reg_alpha=0, reg_lambda=0, 
                                                       seed=0, nthread=-1, silent=True), 
                       param_grid = param_test1, scoring='f1',n_jobs=4,iid=False, cv=10)
gsearch1.fit(gbdtTrain[predictors],gbdtTrain[target])
end = time.time()
print('运行时间：')
(end-start)/60

运行时间：


1.1011951565742493

In [9]:
gsearch1.grid_scores_, gsearch1.best_params_, gsearch1.best_score_

([mean: 0.99035, std: 0.00313, params: {}], {}, 0.9903540098153828)

In [10]:
lgb2 = lgb.LGBMClassifier(
        boosting_type='gbdt', num_leaves=31, max_depth=-1, 
        learning_rate=0.1, n_estimators=500, max_bin=255, subsample_for_bin=50000, 
        min_split_gain=0, min_child_weight=1, min_child_samples=10, 
        subsample=1, subsample_freq=1, colsample_bytree=1, reg_alpha=0, reg_lambda=0, 
        seed=0, nthread=-1, silent=True)
lgb2.fit(gbdtTrain[predictors], gbdtTrain['label'])

LGBMClassifier(boosting_type='gbdt', colsample_bytree=1, drop_rate=0.1,
        is_unbalance=False, learning_rate=0.1, max_bin=255, max_depth=-1,
        max_drop=50, min_child_samples=10, min_child_weight=1,
        min_split_gain=0, n_estimators=500, nthread=-1, num_leaves=31,
        objective='binary', reg_alpha=0, reg_lambda=0, scale_pos_weight=1,
        seed=0, sigmoid=1.0, silent=True, skip_drop=0.5, subsample=1,
        subsample_for_bin=50000, subsample_freq=1, uniform_drop=False,
        xgboost_dart_mode=False)

In [12]:
feaImp = pd.Series(lgb2.booster().feature_importance()).sort_values(ascending=False)#获得重要性不为0的特征
goodFeature = feaImp[feaImp!=0].index
features = gbdtTrain[predictors].columns[goodFeature]
features

D:\Anaconda3\lib\site-packages\sklearn\utils\deprecation.py:70: DeprecationWarning: Function booster is deprecated; Use attribute booster_ instead.
  warnings.warn(msg, category=DeprecationWarning)


Index(['单个顺序号数量_sum', '药品费发生金额_sum', '本次审批金额_sum', '住院开始时间_月_mean',
       '药品费自费金额_sum', '住院开始时间_月_7.0_sum', '基本医疗保险统筹基金支付金额_sum', '非账户支付金额_50',
       '中成药费发生金额_sum', '三目统计项目_3.0_mean',
       ...
       '单个顺序号数量_50', '住院开始时间_月_8.0_75', '操作时间_dayofweek_5.0_mean',
       '住院开始时间_dayofweek_5.0_75', '操作时间_月_25', '医用材料发生金额_75',
       '基本医疗保险个人账户支付金额_50', '治疗费自费金额_mean', '住院开始时间_dayofweek_max',
       '数量_min_50'],
      dtype='object', length=368)

In [18]:
lgb0 = lgb.LGBMClassifier(
        boosting_type='gbdt', num_leaves=15, max_depth=-1, 
        learning_rate=0.1, n_estimators=128, max_bin=255, subsample_for_bin=50000, 
        min_split_gain=0, min_child_weight=1, min_child_samples=10, 
        subsample=1, subsample_freq=1, colsample_bytree=1, reg_alpha=0, reg_lambda=0, 
        seed=0, nthread=-1, silent=True)
lgb0.fit(gbdtTrain[features], gbdtTrain['label'])

LGBMClassifier(boosting_type='gbdt', colsample_bytree=1, drop_rate=0.1,
        is_unbalance=False, learning_rate=0.1, max_bin=255, max_depth=-1,
        max_drop=50, min_child_samples=10, min_child_weight=1,
        min_split_gain=0, n_estimators=128, nthread=-1, num_leaves=15,
        objective='binary', reg_alpha=0, reg_lambda=0, scale_pos_weight=1,
        seed=0, sigmoid=1.0, silent=True, skip_drop=0.5, subsample=1,
        subsample_for_bin=50000, subsample_freq=1, uniform_drop=False,
        xgboost_dart_mode=False)

In [14]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

In [15]:
# 数据归一化
def Scaler(data):
    data = data.fillna(0)
    sc.fit(data[features])
    biaozhunhua = sc.transform(data[features])
    biaozhunhua = pd.DataFrame(biaozhunhua)
    biaozhunhua.columns = features
    return biaozhunhua

In [16]:
ScalerOtherTrain = Scaler(otherTrain)
ScalerOtherTrain

单个顺序号数量_sum  药品费发生金额_sum  本次审批金额_sum  住院开始时间_月_mean  药品费自费金额_sum  \
0        -1.029670    -0.735048   -0.793614      -1.335059    -0.481196   
1        -0.874389    -0.771100   -0.833553      -0.272430    -0.481041   
2         2.124261     1.591161    2.436359       0.160796     0.425375   
3         0.309197     1.047251    0.594760      -0.141969    -0.335637   
4        -0.677700    -0.618933   -0.540096       0.391304    -0.481196   
5        -0.277420    -0.245421   -0.210958      -0.464274    -0.480990   
6         0.002086     0.114185   -0.100876       0.017378    -0.481196   
7         4.253337     4.640061    3.472933       0.940940     1.619452   
8         2.231232     0.408283    1.675027       0.189124    -0.462576   
9        -0.691503    -0.637429   -0.733143       1.080145    -0.481196   
10        1.396165     1.523062    0.955481      -0.575455     1.398741   
11       -0.843333    -0.357659   -0.497456      -1.685974    -0.254399   
12       -0.305025     0.171885   -0.072844      -0.917359    -0.286997   
13       -0.456856    -0.080915   -0.116051       1.928541    -0.481196   
14        0.122860     0.817416    0.500999       2.382469    -0.361169   
15        3.380312     3.623913    2.835601       1.489468     0.848743   
16       -0.750165    -0.388385   -0.498105       0.284490    -0.438178   
17       -0.025519     0.145220    0.002703       1.019767    -0.477328   
18        0.350606     0.327292    0.074470      -0.307230     0.776325   
19       -0.726010    -0.733502   -0.779262      -0.719067    -0.480732   
20        2.231232     3.649550    2.652176       0.442664     1.474151   
21       -0.750165    -0.388385   -0.498105       0.284490    -0.438178   
22       -0.639742    -0.533393   -0.559715       0.143911    -0.396037   
23        1.023490    -0.683386    0.006300       2.877107    -0.348739   
24        2.372710     2.498989    1.894840       1.793988     1.481630   
25       -0.650094    -0.544764   -0.637126      -0.053889     0.612662   
26        0.457577     0.426482    0.248536       0.744658    -0.427192   
27       -0.836432    -0.653232   -0.740380      -0.008898    -0.394851   
28        2.762638     0.940228    2.186945       0.134230    -0.021566   
29       -0.750165    -0.620968   -0.717334      -4.208245    -0.443439   
...            ...          ...         ...            ...          ...   
15470    -0.063477    -0.317384   -0.454955       0.157143     1.210010   
15471    -0.629390     0.132206   -0.124299      -0.182771    -0.481196   
15472    -0.474109    -0.234858   -0.389968       0.219196    -0.299119   
15473    -0.077280    -0.361786   -0.513989       0.199849    -0.182651   
15474    -0.508616    -0.530357   -0.615816      -0.017399    -0.141180   
15475     0.219480    -0.370961   -0.450371       0.238449    -0.481196   
15476     1.233983    -0.543432    0.932809       0.110505    -0.468714   
15477    -0.795023    -0.626384   -0.682679      -0.393184    -0.481196   
15478    -0.443053    -0.408871   -0.511351       0.056479    -0.470828   
15479     0.547295    -0.276815   -0.425850      -0.699022    -0.325166   
15480    -0.370589    -0.453539   -0.535936      -0.211970    -0.452414   
15481    -0.101435    -0.487568   -0.425279       0.152621    -0.481196   
15482    -0.443053    -0.288111   -0.407884      -0.416644    -0.480061   
15483    -0.370589    -0.357858   -0.515851      -0.018323    -0.481196   
15484    -0.529320    -0.503774   -0.551985       0.161355    -0.076086   
15485     0.198775    -0.078501   -0.236911       0.137125    -0.110903   
15486    -0.194603    -0.504830   -0.567523       0.624627    -0.481041   
15487    -0.377490    -0.418409   -0.502002      -0.114002    -0.480990   
15488    -0.284321    -0.241242   -0.393862      -0.342519    -0.481144   
15489    -0.601785    -0.452860   -0.570803      -0.352127     0.479430   
15490     2.400316     0.295851    1.535794      -0.113272    -0.289318   
15491    -0.173899     0.002537 

In [17]:
from sklearn.preprocessing import OneHotEncoder
grd_enc1 = OneHotEncoder()

In [30]:
model=[[x for x in range(15)] for y in range(128)]
model = pd.DataFrame(model)
model = model.T
model

0    1    2    3    4    5    6    7    8    9    10   11   12   13   14   \
0     0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
1     1    1    1    1    1    1    1    1    1    1    1    1    1    1    1   
2     2    2    2    2    2    2    2    2    2    2    2    2    2    2    2   
3     3    3    3    3    3    3    3    3    3    3    3    3    3    3    3   
4     4    4    4    4    4    4    4    4    4    4    4    4    4    4    4   
5     5    5    5    5    5    5    5    5    5    5    5    5    5    5    5   
6     6    6    6    6    6    6    6    6    6    6    6    6    6    6    6   
7     7    7    7    7    7    7    7    7    7    7    7    7    7    7    7   
8     8    8    8    8    8    8    8    8    8    8    8    8    8    8    8   
9     9    9    9    9    9    9    9    9    9    9    9    9    9    9    9   
10   10   10   10   10   10   10   10   10   10   10   10   10   10   10   10   
11   11   11   11   11   11   11   11   11   11   11   11   11   11   11   11   
12   12   12   12   12   12   12   12   12   12   12   12   12   12   12   12   
13   13   13   13   13   13   13   13   13   13   13   13   13   13   13   13   
14   14   14   14   14   14   14   14   14   14   14   14   14   14   14   14   

    15   16   17   18   19   20   21   22   23   24   25   26   27   28   29   \
0     0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
1     1    1    1    1    1    1    1    1    1    1    1    1    1    1    1   
2     2    2    2    2    2    2    2    2    2    2    2    2    2    2    2   
3     3    3    3    3    3    3    3    3    3    3    3    3    3    3    3   
4     4    4    4    4    4    4    4    4    4    4    4    4    4    4    4   
5     5    5    5    5    5    5    5    5    5    5    5    5    5    5    5   
6     6    6    6    6    6    6    6    6    6    6    6    6    6    6    6   
7     7    7    7    7    7    7    7    7    7    7    7    7    7    7    7   
8     8    8    8    8    8    8    8    8    8    8    8    8    8    8    8   
9     9    9    9    9    9    9    9    9    9    9    9    9    9    9    9   
10   10   10   10   10   10   10   10   10   10   10   10   10   10   10   10   
11   11   11   11   11   11   11   11   11   11   11   11   11   11   11   11   
12   12   12   12   12   12   12   12   12   12   12   12   12   12   12   12   
13   13   13   13   13   13   13   13   13   13   13   13   13   13   13   13   
14   14   14   14   14   14   14   14   14   14   14   14   14   14   14   14   

    30   31   32   33   34   35   36   37   38   39   40   41   42   43   44   \
0     0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
1     1    1    1    1    1    1    1    1    1    1    1    1    1    1    1   
2     2    2    2    2    2    2    2    2    2    2    2    2    2    2    2   
3     3    3    3    3    3    3    3    3    3    3    3    3    3    3    3   
4     4    4    4    4    4    4    4    4    4    4    4    4    4    4    4   
5     5    5    5    5    5    5    5    5    5    5    5    5    5    5    5   
6     6    6    6    6    6    6    6    6    6    6    6    6    6    6    6   
7     7    7    7    7    7    7    7    7    7    7    7    7    7    7    7   
8     8    8    8    8    8    8    8    8    8    8    8    8    8    8    8   
9     9    9    9    9    9    9    9    9    9    9    9    9    9    9    9   
10   10   10   10   10   10   10   10   10   10   10   10   10   10   10   10   
11   11   11   11   11   11   11   11   11   11   11   11   11   11   11   11   
12   12   12   12   12   12   12   12   12   12   12   12   12   12   12   12   
13   13   13   13   13   13   13   13   13   13   13   13   13   13   13   13   
14   14   14   14   14   14   14   14   14   14   14   14   14   14   14   14   

    45   46   47   48   49   50   51   52   53   54   55   56   57   58   59   \
0     0    0    0    0    0    0

In [32]:
lgbFeatures0 = pd.DataFrame(lgb0.apply(otherTrain[features]))
grd_enc1.fit(model)
a = grd_enc1.transform(lgbFeatures0)#训练集获得树模型叶子结点特征，离散化
OneHotFeatures = pd.DataFrame(a.toarray())
data_lr_trainPlus00 = pd.concat([ScalerOtherTrain,OneHotFeatures],axis=1)
data_lr_trainPlus00

单个顺序号数量_sum  药品费发生金额_sum  本次审批金额_sum  住院开始时间_月_mean  药品费自费金额_sum  \
0        -1.029670    -0.735048   -0.793614      -1.335059    -0.481196   
1        -0.874389    -0.771100   -0.833553      -0.272430    -0.481041   
2         2.124261     1.591161    2.436359       0.160796     0.425375   
3         0.309197     1.047251    0.594760      -0.141969    -0.335637   
4        -0.677700    -0.618933   -0.540096       0.391304    -0.481196   
5        -0.277420    -0.245421   -0.210958      -0.464274    -0.480990   
6         0.002086     0.114185   -0.100876       0.017378    -0.481196   
7         4.253337     4.640061    3.472933       0.940940     1.619452   
8         2.231232     0.408283    1.675027       0.189124    -0.462576   
9        -0.691503    -0.637429   -0.733143       1.080145    -0.481196   
10        1.396165     1.523062    0.955481      -0.575455     1.398741   
11       -0.843333    -0.357659   -0.497456      -1.685974    -0.254399   
12       -0.305025     0.171885   -0.072844      -0.917359    -0.286997   
13       -0.456856    -0.080915   -0.116051       1.928541    -0.481196   
14        0.122860     0.817416    0.500999       2.382469    -0.361169   
15        3.380312     3.623913    2.835601       1.489468     0.848743   
16       -0.750165    -0.388385   -0.498105       0.284490    -0.438178   
17       -0.025519     0.145220    0.002703       1.019767    -0.477328   
18        0.350606     0.327292    0.074470      -0.307230     0.776325   
19       -0.726010    -0.733502   -0.779262      -0.719067    -0.480732   
20        2.231232     3.649550    2.652176       0.442664     1.474151   
21       -0.750165    -0.388385   -0.498105       0.284490    -0.438178   
22       -0.639742    -0.533393   -0.559715       0.143911    -0.396037   
23        1.023490    -0.683386    0.006300       2.877107    -0.348739   
24        2.372710     2.498989    1.894840       1.793988     1.481630   
25       -0.650094    -0.544764   -0.637126      -0.053889     0.612662   
26        0.457577     0.426482    0.248536       0.744658    -0.427192   
27       -0.836432    -0.653232   -0.740380      -0.008898    -0.394851   
28        2.762638     0.940228    2.186945       0.134230    -0.021566   
29       -0.750165    -0.620968   -0.717334      -4.208245    -0.443439   
...            ...          ...         ...            ...          ...   
15470    -0.063477    -0.317384   -0.454955       0.157143     1.210010   
15471    -0.629390     0.132206   -0.124299      -0.182771    -0.481196   
15472    -0.474109    -0.234858   -0.389968       0.219196    -0.299119   
15473    -0.077280    -0.361786   -0.513989       0.199849    -0.182651   
15474    -0.508616    -0.530357   -0.615816      -0.017399    -0.141180   
15475     0.219480    -0.370961   -0.450371       0.238449    -0.481196   
15476     1.233983    -0.543432    0.932809       0.110505    -0.468714   
15477    -0.795023    -0.626384   -0.682679      -0.393184    -0.481196   
15478    -0.443053    -0.408871   -0.511351       0.056479    -0.470828   
15479     0.547295    -0.276815   -0.425850      -0.699022    -0.325166   
15480    -0.370589    -0.453539   -0.535936      -0.211970    -0.452414   
15481    -0.101435    -0.487568   -0.425279       0.152621    -0.481196   
15482    -0.443053    -0.288111   -0.407884      -0.416644    -0.480061   
15483    -0.370589    -0.357858   -0.515851      -0.018323    -0.481196   
15484    -0.529320    -0.503774   -0.551985       0.161355    -0.076086   
15485     0.198775    -0.078501   -0.236911       0.137125    -0.110903   
15486    -0.194603    -0.504830   -0.567523       0.624627    -0.481041   
15487    -0.377490    -0.418409   -0.502002      -0.114002    -0.480990   
15488    -0.284321    -0.241242   -0.393862      -0.342519    -0.481144   
15489    -0.601785    -0.452860   -0.570803      -0.352127     0.479430   
15490     2.400316     0.295851    1.535794      -0.113272    -0.289318   
15491    -0.173899     0.002537 

In [33]:
from sklearn.linear_model import LogisticRegression
grd_lm = LogisticRegression()

In [34]:
start = time.time()
param_test1 = {
#     'max_iter':np.array([100,500,1000])
}
gsearch1 = GridSearchCV(estimator = grd_lm, 
                       param_grid = param_test1, scoring='f1',n_jobs=4,iid=False, cv=10)
gsearch1.fit(data_lr_trainPlus00,otherTrain[target])
end = time.time()
print('运行时间：')
(end-start)/60

运行时间：


1.7034183382987975

In [35]:
gsearch1.grid_scores_, gsearch1.best_params_, gsearch1.best_score_

([mean: 0.95971, std: 0.00388, params: {}], {}, 0.9597085910513782)

In [36]:
lr = grd_lm
grd_lm.fit(data_lr_trainPlus00,otherTrain[target])

LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_state=None, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False)

In [38]:
lgbFeaturesTest = pd.DataFrame(lgb0.apply(data_tree_test[features]))
scalerTest = Scaler(data_tree_test)
a = grd_enc1.transform(lgbFeaturesTest)#训练集获得树模型叶子结点特征，离散化
OneHotFeaturesTest = pd.DataFrame(a.toarray())
data_lr_test = pd.concat([scalerTest,OneHotFeaturesTest],axis=1)
data_lr_test

单个顺序号数量_sum  药品费发生金额_sum  本次审批金额_sum  住院开始时间_月_mean  药品费自费金额_sum  \
0        3.543784     1.688264    3.881196       0.781080     0.482240   
1        2.102178     0.253995    2.644238       0.631694    -0.306432   
2       -0.654481    -0.620456   -0.663807      -0.313583     0.932626   
3       -0.478407    -0.290825   -0.404456      -0.272782    -0.364218   
4       -0.093245     0.696165    0.347790      -0.604113    -0.264513   
5        0.418470     0.190167    0.000845       0.127810    -0.237558   
6       -0.335347    -0.510545   -0.502034       1.007444    -0.367464   
7       -0.896583    -0.162393   -0.350337       0.411563     0.790506   
8       -0.208793    -0.454498   -0.507788      -1.483174    -0.250450   
9        0.082829    -0.130821    0.054256      -0.473078    -0.367464   
10       2.107680     2.161383    1.709190      -0.064928     0.710588   
11       0.660572     0.856533    0.594939       0.493943     0.482059   
12       5.513611     5.689873    5.012074       0.201333     2.044664   
13       1.177789     0.549671    0.792951      -0.129292    -0.367464   
14      -0.071236     0.423436    0.184501       0.197873    -0.367283   
15      -0.142766    -0.253087   -0.342102      -0.250527    -0.353490   
16      -0.351854    -0.042749    0.155580       0.774644    -0.366923   
17       1.001715     0.947669    0.590165      -0.372364    -0.367464   
18       0.319428     0.186338    0.001561       0.230993    -0.279297   
19       1.183292    -0.398913   -0.546427      -0.272782    -0.367464   
20       0.605549     0.833190    0.543759      -0.309785     2.061522   
21       2.800971    -0.294604    2.190643       0.107898     0.861904   
22      -0.494914    -0.272004   -0.410818      -1.181818    -0.367464   
23       0.693586    -0.286202    2.218898      -0.005721    -0.257436   
24      -0.522425    -0.747006   -0.748845       0.207740    -0.367283   
25       0.759613     0.129344    0.031971       0.127810    -0.333793   
26       2.118685     3.114198    5.298722       0.266049    -0.304359   
27       0.126848     0.596382    0.249675      -0.642093     3.870505   
28      -0.472904     0.072803   -0.080974       1.500382    -0.175626   
29      -0.472904    -0.352832   -0.467204       0.088672    -0.365029   
...           ...          ...         ...            ...          ...   
3970    -1.446814    -1.363321   -1.314511       0.127810    -0.367464   
3971    -1.424805    -1.341831   -1.326412       0.938532    -0.367464   
3972    -1.265237    -1.310760   -1.269376       1.262821    -0.367464   
3973    -1.226721    -1.045109   -1.061863       2.776170    -0.367464   
3974    -1.226721    -1.298280   -1.273645       3.532844    -0.367464   
3975    -0.781034     1.932448    1.224158       3.042028    -0.273618   
3976     1.304342    -0.623311    0.529042       3.154507    -0.367464   
3977     0.545023    -0.822239    0.473199       3.256012    -0.365841   
3978    -1.468823    -1.363321   -1.325456       1.262821    -0.367464   
3979    -0.665485     0.171776    0.007476       2.900215    -0.367058   
3980    -1.331265    -1.363321    0.425542       3.532844    -0.367464   
3981    -0.698499    -0.815057   -0.852473       4.717203    -0.199245   
3982    -1.144187    -1.273256   -1.253524       2.397833    -0.367464   
3983    -0.659983    -0.985321   -0.819700       3.169640    -0.367464   
3984    -0.737015     1.094970    0.562605       3.594196    -0.367464   
3985    -1.144187    -0.829657   -0.587050       2.397833    -0.367464   
3986    -1.452316    -1.329723   -1.316683       2.397833    -0.367464   
3987    -1.380786    -1.261532   -1.258303       3.532844    -0.367464   
3988     0.269908     0.925181    0.554520       4.226462     0.745160   
3989    -1.474325    -1.345586   -1.330855       3.532844    -0.367464   
3990    -1.221219    -0.833553    0.077943       4.289518    -0.367464   
3991    -1.358777    -1.363321    0.233206       5.348862    -0.367464   
3992    -1

In [39]:
lrp = grd_lm.predict(data_lr_test)

In [40]:
data_tree_test['lrpre'] = lrp
data_tree_test['lrpre'].value_counts()

0    3559
1     441
Name: lrpre, dtype: int64

In [41]:
lrRes = data_tree_test[['个人编码','lrpre']]
lrRes.to_csv('gbdt+lr.csv',index=None,header=None)